# Follow-Me Logic
Simple script for testing abstract follow-me logic.

# Imports

In [598]:
import numpy as np
import pandas as pd

import sys

# plotly
import plotly.graph_objects as go
import plotly.express as px
import plotly.figure_factory as ff

# tuple for hints
from typing import Tuple

# Definitions

## Constants

In [599]:
FLT_EPSILON = sys.float_info.epsilon

## Helper functions

### Angle wrapping Functions

In [600]:
"""
Wraps the input angle between [-pi, pi]
"""
def wrap_pi(angle: float) -> float:
    return (angle + np.pi) % (2 * np.pi) - np.pi


"""
Unwraps the next angle to be within [-pi, pi] difference away from the last_angle

Implementation from : https://github.com/PX4/PX4-Autopilot/blob/db7430aa65491b501290111e839a9acf70bd6287/src/lib/matrix/matrix/helper_functions.hpp#L141-L152
"""
def unwrap_pi(last_angle: float, next_angle: float) -> float:
  return (last_angle + wrap_pi(next_angle - last_angle))

### Sign

In [601]:
def sign(val: float, deadzone: float = 0.) -> int:
    """
    Returns the sign of a value, or zero if within deadzone.
    """

    return int(val > deadzone) - int(val < -deadzone)

## Maximum Velocity Calculation

In [602]:
"""
Compute the maximum possible speed on the track given the desired speed, remaining distance, the maximum acceleration and the maximum jerk.
We assume a constant acceleration profile with a delay of 2*accel/jerk (time to reach the desired acceleration from opposite max acceleration)

Equation to solve: vel_final^2 = vel_initial^2 - 2*accel*(x - vel_initial*2*accel/jerk)

Implementation from : https://github.com/PX4/PX4-Autopilot/blob/f9d8c613b048f58eb3110e9af13cb3a89c4c866f/src/lib/mathlib/math/TrajMath.hpp#L48-L71
"""
def computeMaxSpeedFromDistance(jerk: float, accel: float, braking_distance: float, final_speed: float):
  b = 4.0 * (accel ** 2) / jerk
  c = -2.0 * accel * braking_distance - final_speed ** 2
  max_speed = 0.5 * (-b + (b ** 2 - 4.0 * c) ** 0.5)
  return max(max_speed, final_speed)

## Jerk limited Trajectory Generator Library (Velocity Smoothing)

In [603]:
# https://github.com/Auterion/Flight_Control_Prototyping_Scripts/blob/master/trajectory_generator/VelocitySmoothing.py

"""
File: VelocitySmoothing.py
Author: Mathieu Bresciani
Email: brescianimathieu@gmail.com
Github: https://github.com/bresch
Description:
    Given a desired velocity setpoint v_d, the trajectory generator computes
    a time-optimal trajectory satisfaying the following variable constraints:
    - j_max : maximum jerk
    - a_max : maximum acceleration
    - v_max : maximum velocity
    - a0 : initial acceleration
    - v0 : initial velocity
    - v3 : final velocity
    The hard constraint used to generate the optimizer is:
    - a3 = 0.0 : final acceleration
    The trajectory generated is made by three parts:
    1) Increasing acceleration during T1 seconds
    2) Constant acceleration during T2 seconds
    3) Decreasing acceleration during T3 seconds
"""

from __future__ import print_function

from numpy import *
import sys
import math
import matplotlib.pylab as plt

FLT_EPSILON = sys.float_info.epsilon
NAN = float('nan')
verbose = True

if verbose:
    def verboseprint(*args):
        # Print each argument separately so caller doesn't need to
        # stuff everything to be printed into a single string
        for arg in args:
            print(arg, end=" ")
        print("")
else:
    verboseprint = lambda *a: None      # do-nothing function

class VelocitySmoothing(object):

    def setState(self, a0, v0, x0):
        self._accel = a0
        self._vel = v0
        self._pos = x0

    def __init__(self, a0, v0, x0):
        self._jerk = 0.0
        self._accel = self._at0 = a0
        self._vel = self._vt0 = v0
        self._pos = self._xt0 = x0
        self._vel_sp = 0.0
        self._d = 0

        self._max_jerk = 9.0
        self._max_accel = 3.0
        self._max_vel = 5.0

        self._T1 = 0.0
        self._T2 = 0.0
        self._T3 = 0.0

    def computeT1(self, a0, v3, j_max, a_max):
        delta = 2.0*a0**2 + 4.0*j_max*v3

        if delta < 0.0:
            verboseprint('Complex roots\n')
            return (0.0, True);

        T1_plus = (-a0 + 0.5*sqrt(delta))/j_max
        T1_minus = (-a0 - 0.5*sqrt(delta))/j_max

        # verboseprint('T1_plus = {}, T1_minus = {}'.format(T1_plus, T1_minus))
        # Use the solution that produces T1 >= 0 and T3 >= 0
        T3_plus = a0/j_max + T1_plus
        T3_minus = a0/j_max + T1_minus

        if T1_plus >= 0.0 and T3_plus >= 0.0:
            T1 = T1_plus
        elif T1_minus >= 0.0 and T3_minus >= 0.0:
            T1 = T1_minus
        else:
            verboseprint("Warning")
            T1 = 0.0

        (T1, trapezoidal) = self.saturateT1ForAccel(a0, a_max, j_max, T1)

        return (T1, trapezoidal)

    def saturateT1ForAccel(self, a0, a_max, j_max, T1):
        trapezoidal = False
        # Check maximum acceleration, saturate and recompute T1 if needed
        a1 = a0 + j_max*T1
        if a1 > a_max:
            T1 = (a_max - a0) / j_max
            trapezoidal = True
        elif a1 < -a_max:
            T1 = (-a_max - a0) / j_max
            trapezoidal = True

        return (T1, trapezoidal)

    def computeT3(self, T1, a0, j_max):
        T3 = a0/j_max + T1

        return T3

    def computeT2(self, T1, T3, a0, v3, j_max):
        T2 = 0.0

        den = T1*j_max + a0
        if abs(den) > FLT_EPSILON:
            T2 = (-0.5*T1**2*j_max - T1*T3*j_max - T1*a0 + 0.5*T3**2*j_max - T3*a0 + v3)/den

        return T2

    def updateDurations(self):

        if (abs(self._accel) > self._max_accel):
            verboseprint("Should be double deceleration profile!")
        # Depending of the direction, start accelerating positively or negatively
        # For this, we need to predict what would be the velocity at zero acceleration
        # because it could be that the current acceleration is too high and that we need
        # to start reducing the acceleration directly even if sign(v_d - v_T) < 0
        do_stop_check = False
        if abs(self._accel) > FLT_EPSILON and do_stop_check:
            j_zero_acc = -sign(self._accel) * abs(self._max_jerk);
            t_zero_acc = -self._accel / j_zero_acc;
            vel_zero_acc = self._vel + self._accel * t_zero_acc + 0.5 * j_zero_acc * t_zero_acc * t_zero_acc;
            verboseprint("vel_zero_acc = {}\tt_zero_acc = {}".format(vel_zero_acc, t_zero_acc))
            verboseprint("vel = {}, accel = {}, jerk = {}".format(self._vel, self._accel, j_zero_acc))
        else:
            vel_zero_acc = self._vel

        self._d = sign(self._vel_sp - vel_zero_acc)
        jerk = self._d*self._max_jerk

        if abs(jerk) < 0.5 * self._max_jerk:
            self._T1 = self._T2 = self._T3 = 0.0
            # print("Return")
            return

        self._at0 = self._accel
        self._vt0 = self._vel
        self._xt0 = self._pos

        delta_v = self._vel_sp - self._vel
        # Compute increasing acceleration time
        (T1, trapezoidal) = self.computeT1(self._accel, delta_v, jerk, self._max_accel)
        # Compute decreasing acceleration time
        T3 = self.computeT3(T1, self._accel, jerk);
        # Compute constant acceleration time
        if trapezoidal:
            T2 = self.computeT2(T1, T3, self._accel, delta_v, jerk)

        else:
            T2 = 0.0

        self._T1 = T1
        self._T2 = T2
        self._T3 = T3

    def update(self, vel_sp):
        self._vel_sp = clip(vel_sp, -self._max_vel, self._max_vel)
        self.updateDurations()

    def evaluatePoly(self, j, a0, v0, x0, t, d):
        jt = d*j
        at = a0 + jt*t
        vt = v0 + a0*t + 0.5*jt*t**2
        xt = x0 + v0*t + 0.5*a0*t**2 + 1.0/6.0*jt*t**3

        return (jt, at, vt, xt)

    def evaluateTraj(self, dt):
        """evaluate trajectory for the given time
        """
        j = self._max_jerk
        d = self._d
        t = dt

        if t <= self._T1:
            t1 = t
            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(j, self._at0, self._vt0, self._xt0, t1, d)

        elif t <= self._T1 + self._T2:
            t1 = self._T1
            t2 = t - self._T1

            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(j, self._at0, self._vt0, self._xt0, t1, d)
            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(0.0, self._accel, self._vel, self._pos, t2, 0.0)

        elif t <= self._T1 + self._T2 + self._T3:
            t1 = self._T1
            t2 = self._T2
            t3 = t - self._T1 - self._T2

            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(j, self._at0, self._vt0, self._xt0, t1, d)
            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(0.0, self._accel, self._vel, self._pos, t2, 0.0)
            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(j, self._accel, self._vel, self._pos, t3, -d)

        else:
            # TODO : do not recompute if the sequence has already been completed
            t1 = self._T1
            t2 = self._T2
            t3 = self._T3

            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(j, self._at0, self._vt0, self._xt0, t1, d)
            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(0.0, self._accel, self._vel, self._pos, t2, 0.0)
            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(j, self._accel, self._vel, self._pos, t3, -d)
            (self._jerk, self._accel, self._vel, self._pos) = self.evaluatePoly(0.0, 0.0, self._vel_sp, self._pos, t - self._T1 - self._T2 - self._T3, 0.0)

        return (self._jerk, self._accel, self._vel, self._pos)

## Follow-me object

In [604]:
'''
Python implementation of Follow Target module in the PR : https://github.com/PX4/PX4-Autopilot/pull/19260

It implements
1. Jerk limited orbit trajectory generation
2. Follow angle setting
3. Maximum velocity setting

It doesn't implement
1. Taret position velocity 2nd order reference model filtering (We assume we have a perfectly filtered 100Hz incoming data)
2. Follow Distance, Height adjustments
3. 
'''

class FollowMe:

    # CONSTANTS

    # When the target speed is above this threshold, we consider the target's orientation valid estimate
    TARGET_SPEED_THRESHOLD = 1.5  # [m/s]

    # MAX Jerk allowed for the orbit trajectory
    ORBIT_TRAJECTORY_MAX_JERK = 4.0

    # MAX Acceleration allowed for the orbit trajectory
    ORBIT_TRAJECTORY_MAX_ACCEL = 2.0

    def __init__(self,
            max_tangential_speed: float,  # [m/s]
            follow_distance: float        # [m]
        ):

        # the max linear speed we allow transitions about the orbit radius. it is
        # divided by the current follow distance to give the max rotational speed
        self._max_tangential_speed = max_tangential_speed

        self._follow_distance = follow_distance

        # arbitrarily initialize the target orientation to north and follow angle
        # to "behind"
        self.reset_angles(
            target_orientation = 0.,
            follow_angle = np.pi
        )

        # Initialize VelocitySmoothing object with acc, vel and pos set to 0.0
        self._orbit_trajectory_generator = VelocitySmoothing(0.0, 0.0, 0.0)


    # PRIVATE METHODS
    def _update_target_orientation(self,
            current_target_course: float,  # [rad]
            current_target_orientation: float,  # [rad]
            target_speed: float  # [m/s]
        ) -> float:

        if(target_speed > self.TARGET_SPEED_THRESHOLD):
          return current_target_course # Hard reset
        else:
          # If below threshold, return current tracked target orientation (freeze the orientation)
          return current_target_orientation

    """
    Updates orbit angle!
    """
    def _update_orbit_angle(self,
            current_orbit_angle: float,  # [rad]
            target_orientation: float,  # [rad]
            time_step: float  # [s]
        ) -> Tuple[float, float]:

        # Raw target orbit (setpoint) angle, unwrapped to be relative to the previous orbit angle setpoint
        unwrapped_raw_orbit_angle = unwrap_pi(current_orbit_angle, target_orientation + self._follow_angle)
        
        # Save the raw commanded orbit angle setpoint (To check how well generated trajectory follows it)
        self._orbit_angle_raw = unwrapped_raw_orbit_angle

        # Update limits for orbit trajectory generator
        self._orbit_trajectory_generator._max_jerk = self.ORBIT_TRAJECTORY_MAX_JERK / self._follow_distance
        self._orbit_trajectory_generator._max_accel = self.ORBIT_TRAJECTORY_MAX_ACCEL / self._follow_distance
        self._orbit_trajectory_generator._max_vel = self._max_tangential_speed / self._follow_distance

        remaining_angle = unwrapped_raw_orbit_angle - current_orbit_angle
        remaining_angle_sign = np.sign(remaining_angle)

        # Calculate max rate assuming we want final speed to be 0 when we reach target orbit angle. Remaining angle input must be positive (take absolute value), otherwise it can return NaN
        max_rate = computeMaxSpeedFromDistance(self._orbit_trajectory_generator._max_jerk, self._orbit_trajectory_generator._max_accel, abs(remaining_angle), 0.0)

        # Feed in the velocity setpoint to be smoothed
        self._orbit_trajectory_generator.update(max_rate * remaining_angle_sign)

        # Take a step in integrating the trajectory
        jerk, accel, vel, pos = self._orbit_trajectory_generator.evaluateTraj(time_step)

        # Debug printing
        # print("{:.2f} {:.2f} {:.2f} {:.2f} {:.2f} {:.2f} | Cur : {:.2f} Remain : {:.2f} | Target Ori : {:.2f}".format(max_rate, remaining_angle_sign, jerk, accel, vel, pos, current_orbit_angle, remaining_angle, target_orientation))

        return pos


    def _follow_position_offset(self,
            orbit_angle: float
        ) -> np.ndarray:
        """
        Calculates and returns the follow position w.r.t. target position.
        """

        return self._follow_distance * np.array([
            np.cos(orbit_angle),
            np.sin(orbit_angle)
        ])

    # PUBLIC METHODS

    def reset_angles(self,
            target_orientation: float,  # [rad]
            follow_angle: float  # [rad]
        ):
        """
        Reset the target orientation, follow angle, and orbit angle
        """

        # the target frame, for now derived from its course angle [rad]
        self._target_orientation = target_orientation

        # angle (positive clock-wise) in [-pi, pi] from the target course where the
        # drone should orient itself [rad]
        self._follow_angle = follow_angle

        # angle from North on follow orbit where the drone should be [rad] 
        self._orbit_angle = wrap_pi(self._target_orientation + self._follow_angle)


    def get_speed_threshold(self) -> float:
        return self.TARGET_SPEED_THRESHOLD


    def get_follow_angle(self) -> float:
        return self._follow_angle


    def get_target_orientation(self) -> float:
        return self._target_orientation


    def get_orbit_angle(self) -> float:
        return self._orbit_angle

    def get_orbit_angle_raw(self) -> float:
        return self._orbit_angle_raw

    """
    Calculates the desired 2D follow position and velocity. This is the main update function for the class : update().
    """
    def calculate_follow_pose(self,
            target_position: np.ndarray,  # [m]
            target_velocity: np.ndarray,  # [m/s]
            follow_angle_command: float,  # from the operator [rad]
            time_step: float  # time since last call [s]
        ) -> Tuple[np.ndarray, np.ndarray]:
        
        # TODO: handle time_step bounds / resets

        target_speed = np.linalg.norm(target_velocity[:2])
        current_target_course = np.arctan2(target_velocity[1], target_velocity[0])

        # Estimate target's orientation
        self._target_orientation = self._update_target_orientation(
            current_target_course = current_target_course,
            current_target_orientation = self._target_orientation,
            target_speed = target_speed
        )

        # Directly set follow angle as the commanded value
        self._follow_angle = follow_angle_command

        # Update the commanded orbit angle considering *current target orientation
        # and follow angle, with Jerk limited trajectory generator this is what will actually
        # command the drone's desired position
        self._orbit_angle = self._update_orbit_angle(
            current_orbit_angle = self._orbit_angle,
            target_orientation = self._target_orientation,
            time_step = time_step
        )

        follow_position_offset = self._follow_position_offset(
            orbit_angle = self._orbit_angle
        )
        
        position_setpoint_raw = target_position + follow_position_offset

        # this velocity will be taken as a feed-forward term in the drone's position
        # / velocity control loops.
        velocity_setpoint_raw = target_velocity # + lever arm component (transition rate * radius + vehicle course rate * radius)

        return position_setpoint_raw, velocity_setpoint_raw

## Test Data

Generate target test data. We assume here that it is nicely filtered at 100Hz.

### Circle

In [605]:
def generate_target_poses_on_circle() -> Tuple[np.ndarray, np.ndarray, np.ndarray]:
    """
    Generates target poses along a circle.
    Return Tuple( target positions, target velocities, time vector )
    """

    time_start = 0.  # [s]
    time_stop = 50.  # [s]
    time_step = 0.01  # [s]

    circle_radius = 30.  # [m]
    accel_period_1 = [1.3, 7.]  # [s]
    accel_period_2 = [18., 25.]  # [s]

    # convert constant radius and tangential acceleration to reasonable angular acceleration
    linear_accel = 1.5  # [m/s^2]
    angular_accel = linear_accel / circle_radius  # [rad/s^2]

    time_vector = np.arange(time_start, time_stop, time_step)
    len_time = len(time_vector)

    # allocate and initialize
    angle = np.zeros(len_time)
    angular_rate = np.zeros(len_time)
    target_position = np.zeros([2, len_time])
    target_velocity = np.zeros([2, len_time])

    # simulate target motion
    for k in range(len_time):
        
        # system input calculation
        if time_vector[k] >= accel_period_1[0] and time_vector[k] < accel_period_1[1]:
            # first accelerate clockwise ...
            angular_accel_k = angular_accel  # [rad/s^2]

        elif time_vector[k] >=  accel_period_2[0] and time_vector[k] < accel_period_2[1]:
            # ... and then reverse after a while
            angular_accel_k = -angular_accel  # [rad/s^2]

        else:
            angular_accel_k = 0.  # [rad/s^2]

        # state output
        target_position[0, k] = circle_radius * np.cos(angle[k])
        target_position[1, k] = circle_radius * np.sin(angle[k])
        target_velocity[0, k] = circle_radius * -np.sin(angle[k]) * angular_rate[k]
        target_velocity[1, k] = circle_radius * np.cos(angle[k]) * angular_rate[k]

        # euler integration
        if k < len_time - 1:
            angle[k + 1] = angle[k] + angular_rate[k] * time_step
            angular_rate[k + 1] = angular_rate[k] + angular_accel_k * time_step

    return target_position, target_velocity, time_vector

### Fast Circle and Other

In [606]:
def generate_target_poses_on_fast_circle() -> Tuple[np.ndarray, np.ndarray, np.ndarray]:
    """
    Generates target poses along a circle.
    Return Tuple( target positions, target velocities, time vector )
    """

    time_start = 0.  # [s]
    time_stop = 50.  # [s]
    time_step = 0.01  # [s]

    circle_radius = 60.  # [m]
    accel_period_1 = [1.3, 7.]  # [s]
    accel_period_2 = [18., 25.]  # [s]

    # Time until, acceleration value
    accel_list = [[5., 6.,], [10., -5], [12., -9], [17, 8]]
    accel_idx = 0

    # convert constant radius and tangential acceleration to reasonable angular acceleration
    linear_accel = 6  # [m/s^2]
    angular_accel = linear_accel / circle_radius  # [rad/s^2]

    time_vector = np.arange(time_start, time_stop, time_step)
    len_time = len(time_vector)

    # allocate and initialize
    angle = np.zeros(len_time)
    angular_rate = np.zeros(len_time)
    target_position = np.zeros([2, len_time])
    target_velocity = np.zeros([2, len_time])

    angular_accel_k = 0.

    angular_accel_k = accel_list[0][1] # Initialize according to the list.

    # simulate target motion
    for k in range(len_time):
        if(k*time_step > accel_list[accel_idx][0]):
          print(k, )
          accel_idx += 1
          # if(accel_idx == len(accel_list)):
          #     angular_accel_k = 0.
          # else:
          #     angular_accel_k = accel_list[accel_idx][1]
        # # system input calculation
        # if time_vector[k] >= accel_period_1[0] and time_vector[k] < accel_period_1[1]:
        #     # first accelerate clockwise ...
        #     angular_accel_k = angular_accel  # [rad/s^2]

        # elif time_vector[k] >=  accel_period_2[0] and time_vector[k] < accel_period_2[1]:
        #     # ... and then reverse after a while
        #     angular_accel_k = -angular_accel  # [rad/s^2]

        # else:
        #     angular_accel_k = 0.  # [rad/s^2]

        # state output
        target_position[0, k] = circle_radius * np.cos(angle[k])
        target_position[1, k] = circle_radius * np.sin(angle[k])
        target_velocity[0, k] = circle_radius * -np.sin(angle[k]) * angular_rate[k]
        target_velocity[1, k] = circle_radius * np.cos(angle[k]) * angular_rate[k]

        # euler integration
        if k < len_time - 1:
            angle[k + 1] = angle[k] + angular_rate[k] * time_step
            angular_rate[k + 1] = angular_rate[k] + angular_accel_k * time_step

    return target_position, target_velocity, time_vector

### Jerky trajectory

In [607]:
def generate_jerky_target_poses() -> Tuple[np.ndarray, np.ndarray, np.ndarray]:
    """
    Generates target poses along a jerky trajectory
    Return Tuple( target positions, target velocities, time vector )
    """

    time_start = 0.  # [s]
    time_stop = 50.  # [s]
    time_step = 0.01  # [s]

    time_vector = np.arange(time_start, time_stop, time_step)
    len_time = len(time_vector)

    # allocate and initialize
    target_position = np.zeros([2, len_time])
    target_velocity = np.zeros([2, len_time])

    # 1. First move very fast and stop
    for t in range(int(time_start/time_step) + 1, int(2.0/time_step)):
      target_velocity[:, t] = np.array([10., 1.]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step
    
    for t in range(int(2.0/time_step), int(2.5/time_step)):
      target_velocity[:, t] = np.array([0., 0.]) # [m/s]
      target_position[:, t] = target_position[:, t-1]
    
    # 2. Move at Threshold velocity, then return
    for t in range(int(2.5/time_step), int(5.5/time_step)):
      target_velocity[:, t] = np.array([-FollowMe.TARGET_SPEED_THRESHOLD, 0.]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step
    
    for t in range(int(5.5/time_step), int(6.5/time_step)):
      target_velocity[:, t] = np.array([0., 0.]) # [m/s]
      target_position[:, t] = target_position[:, t-1]

    for t in range(int(6.5/time_step), int(9.5/time_step)):
      target_velocity[:, t] = np.array([FollowMe.TARGET_SPEED_THRESHOLD, 0.]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step

    # 3. Move at Threshold / 2 velocity, then return
    for t in range(int(9.5/time_step), int(12.5/time_step)):
      target_velocity[:, t] = np.array([0.,-(FollowMe.TARGET_SPEED_THRESHOLD)/2]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step
    
    for t in range(int(12.5/time_step), int(13.5/time_step)):
      target_velocity[:, t] = np.array([0., 0.]) # [m/s]
      target_position[:, t] = target_position[:, t-1]

    for t in range(int(13.5/time_step), int(16.5/time_step)):
      target_velocity[:, t] = np.array([0., (FollowMe.TARGET_SPEED_THRESHOLD)/2]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step

    # 4. Move at Threshold velocity in a triangle
    for t in range(int(16.5/time_step), int(19.5/time_step)):
      target_velocity[:, t] = np.array([FollowMe.TARGET_SPEED_THRESHOLD * np.cos(np.deg2rad(60)), FollowMe.TARGET_SPEED_THRESHOLD * np.sin(np.deg2rad(60))]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step
    
    for t in range(int(19.5/time_step), int(22.5/time_step)):
      target_velocity[:, t] = np.array([FollowMe.TARGET_SPEED_THRESHOLD * np.cos(np.deg2rad(60)), -FollowMe.TARGET_SPEED_THRESHOLD * np.sin(np.deg2rad(60))]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step

    for t in range(int(22.5/time_step), int(25.5/time_step)):
      target_velocity[:, t] = np.array([-FollowMe.TARGET_SPEED_THRESHOLD, 0.]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step

    # 5. Move in a circle trajectory in Threshold velocity
    spin_speed = 1 # [rad/s]
    for t in range(int(25.5/time_step), int(30.5/time_step)):
      target_velocity[:, t] = np.array([FollowMe.TARGET_SPEED_THRESHOLD * np.cos(spin_speed * t*time_step), FollowMe.TARGET_SPEED_THRESHOLD * np.sin(spin_speed * t*time_step)]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step

    # 6. Move in a tighter circle in different direction
    spin_speed = 1.5
    for t in range(int(30.5/time_step), int(35.5/time_step)):
      target_velocity[:, t] = np.array([-FollowMe.TARGET_SPEED_THRESHOLD * 3 * np.cos(spin_speed * t*time_step), -FollowMe.TARGET_SPEED_THRESHOLD * 3 * np.sin(spin_speed * t*time_step)]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step
    
    # 7. Move in multiple directions (test target heading tracking)
    heading_change_dt = 1.0
    last_heading_change_at = 35.5
    cur_heading = 0. # [rad]
    for t in range(int(35.5/time_step), int(50.0/time_step)):
      if(t*time_step > last_heading_change_at + heading_change_dt):
          cur_heading = (2*np.pi*np.random.random() - np.pi) # In range [-np.pi, np.pi]
          last_heading_change_at = t*time_step
      target_velocity[:, t] = np.array([FollowMe.TARGET_SPEED_THRESHOLD * np.cos(cur_heading), FollowMe.TARGET_SPEED_THRESHOLD * np.sin(cur_heading)]) # [m/s]
      target_position[:, t] = target_position[:, t-1] + target_velocity[:, t] * time_step
    

    return target_position, target_velocity, time_vector

# Simulation

## Generate target data

In [664]:
target_position, target_velocity, time_vector = generate_target_poses_on_circle()
# target_position, target_velocity, time_vector = generate_target_poses_on_fast_circle()
# target_position, target_velocity, time_vector = generate_jerky_target_poses()

### Visualize target trajectory

In [665]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=target_position[0,:], y=target_position[1,:],
                    mode='lines+markers',
                    name='Position'))

fig.show()

## Set up Follow Angle Commands

In [679]:
follow_angles = np.zeros([len(time_vector)])

# 1. Follow angle changing case
'''
Behaviour would be to : 
1. Set to 0 at 1/4th of time interval
2. Set to 180 at 2/4th
3. Set to 30 at 3/4th
'''

len_time_div_4 = len(time_vector) / 4
for i in range(len(follow_angles)):
  if(i < len_time_div_4):
    follow_angles[i] = np.deg2rad(135)
  elif(i < len_time_div_4 * 2):
    follow_angles[i] = np.deg2rad(0)
  elif(i < len_time_div_4 * 3):
    follow_angles[i] = np.deg2rad(180)
  else:
    follow_angles[i] = np.deg2rad(30)

# 2. Follow angle fixed case
follow_angles[:] = np.deg2rad(180) # right behind the target

### Visualize follow angle command

In [680]:
fig = go.Figure()

# Plot simple 2D trajectory
fig.add_trace(go.Scatter(x=time_vector[:], y=follow_angles))
fig.update_layout(title_text="Follow angle vs Time")

fig.show()

## Setup the follow-me object

In [681]:
max_tangential_speed = 15.  # [m/s]
follow_distance = 8.

follow_me = FollowMe(max_tangential_speed = max_tangential_speed, follow_distance = follow_distance)

### Initialize values inside Follow-me

In [682]:
# initialize the angular targets (also initializes the orbit angle)
follow_me.reset_angles(
    target_orientation = 0.,  # [rad]
    follow_angle = follow_angles[0]  # [rad]
)

## Run the data through the follow me logic

In [683]:
len_time = len(time_vector)

position_setpoint = np.zeros([2, len_time])
velocity_setpoint = np.zeros([2, len_time])

raw_follow_position = np.zeros([2, len_time])

follow_angle = np.zeros(len_time)
target_orientation = np.zeros(len_time)
orbit_angle = np.zeros(len_time)
orbit_angle_raw = np.zeros(len_time) # Raw commanded value that Trajectory generator tries to follow

target_orientation_truth = np.zeros(len_time)

for k in range(len_time):

    if k == 0:
        time_step = 0.0
    else:
        time_step = time_vector[k] - time_vector[k-1]

    # update the position and velocity setpoints
    position_setpoint[:, k], velocity_setpoint[:, k] = follow_me.calculate_follow_pose(
        target_position = target_position[:, k],
        target_velocity = target_velocity[:, k],
        follow_angle_command = follow_angles[k], # Dynamic Follow Angle manipulation
        time_step = time_step
    )

    # output current follow-me angles (could be delayed from commands)
    follow_angle[k] = follow_me.get_follow_angle()

    target_orientation[k] = follow_me.get_target_orientation()

    orbit_angle[k] = follow_me.get_orbit_angle()

    orbit_angle_raw[k] = follow_me.get_orbit_angle_raw()

    # ground truth target orientation
    target_orientation_truth[k] = np.arctan2(target_velocity[1, k], target_velocity[0, k])

    # ground truth orbit angle
    raw_follow_position[:, k] = target_position[:, k] + \
        follow_distance * np.array([np.cos(orbit_angle_raw[k]), np.sin(orbit_angle_raw[k])])

Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 
Warning 


# Visualization

## Position animation
Slider animation of position

In [684]:
# sample data at time interval 
slider_time_interval = 0.1  # s

# the index interval for the chosen slider time interval
k_interval = int(slider_time_interval / time_step)

num_slider_frames = int(np.floor(len_time / k_interval)) + 1

# this sets the duration each frame takes when animating with the 'play' button [ms]
# (slider_time_interval is 'real time')
step_duration = 0.5 * slider_time_interval * 1e3

# this sets the duration each frame takes when manually moving the slider [ms]
slider_step_duration = 20

# PLOTTING OPTIONS

# plot tail histories on positions
plot_tails = False  # XXX: these don't work as expected fully ATM
len_tail_s = 10.  # [s]
len_tail_k = int(len_tail_s / time_step)

# make the figure (it is just a dict!)
fig_dict = {
    'data': [],
    'layout': {},
    'frames': []
}

# fill in most of the layout
fig_dict['layout']['xaxis'] = {'title': 'East Position [m]'}
fig_dict['layout']['yaxis'] = {'title': 'North Position [m]'}
fig_dict['layout']['hovermode'] = 'closest'
fig_dict['layout']['updatemenus'] = [
   {
       'buttons': [
           # play button
           {
                'args': [
                    None,
                    {
                        'frame': {'duration': step_duration, 'redraw': False},
                        'fromcurrent': True,
                        'transition': {'duration': step_duration, 'easing': 'linear'}
                    }
                ],
                'label': 'Play',
                'method': 'animate'
            },
            # pause button
            {
                'args': [
                    [None], 
                    {
                        'frame': {'duration': 0, 'redraw': False},
                        'mode': 'immediate',
                        'transition': {'duration': 0}
                    }
                ],
                'label': 'Pause',
                'method': 'animate'
            }
        ],
        # 'direction': 'left',
        # 'pad': {'r': 10, 't': 87},
        'showactive': False,
        'type': 'buttons',
        # 'x': 0.1,
        # 'xanchor': 'right',
        # 'y': 0,
        # 'yanchor': 'top'
   }
]

# empty sliders dict
sliders_dict = {
    'active': 0,  # the initially active frame
    'yanchor': 'top',
    'xanchor': 'left',
    'currentvalue': {
        'visible': True
    },
    # 'transition': {'duration': step_duration, 'easing': 'linear'},
    'pad': {'b': 10, 't': 50},
    'len': 0.9,
    'x': 0.1,
    'y': 0,
    'steps': []
}

# update global axis range
xaxis_max = np.max([np.max(target_position[1, :]), np.max(raw_follow_position[1, :]), np.max(position_setpoint[1, :])])
xaxis_min = np.min([np.min(target_position[1, :]), np.min(raw_follow_position[1, :]), np.min(position_setpoint[1, :])])
yaxis_max = np.max([np.max(target_position[0, :]), np.max(raw_follow_position[0, :]), np.max(position_setpoint[0, :])])
yaxis_min = np.min([np.min(target_position[0, :]), np.min(raw_follow_position[0, :]), np.min(position_setpoint[0, :])])

# make frames
for k in range(0, len_time, k_interval):

    # initialize the frame
    frame = {'data': [], 'name': f'{time_vector[k]:3.1f}'}

    # tail indices
    k_start = max(k - len_tail_k, 0)
    k_end = min(k + 1, len_time)

    # populate the frame data list with traces

    # marker for target position
    frame['data'].append(
        go.Scatter(
            x = [target_position[1, k]],
            y = [target_position[0, k]],
            marker = dict({
                'symbol': 'circle',
                'size': 15,
                'color': 'rgb(180, 180, 180)'  # gray
            }),
            name = 'Target position'
        )
    )

    # orbit perimeter around target position
    orbit_perimeter_y = [target_position[0, k] + follow_distance * np.cos(angle) for angle in np.linspace(-np.pi, np.pi, 201)]
    orbit_perimeter_x = [target_position[1, k] + follow_distance * np.sin(angle) for angle in np.linspace(-np.pi, np.pi, 201)]
    frame['data'].append(
        go.Scatter(
            x = orbit_perimeter_x,
            y = orbit_perimeter_y,
            line = dict({
                'color': 'rgb(180, 180, 180)'  # gray
            }),
            name = 'Orbit perimeter'
        )
    )

    # TARGET ORIENTATION
    # - - - - - - - - - -

    # true target orientation
    frame['data'].append(
        go.Scatter(
            x = np.array([0., np.sin(target_orientation_truth[k]) * follow_distance]) + target_position[1, k],
            y = np.array([0., np.cos(target_orientation_truth[k]) * follow_distance]) + target_position[0, k],
            name = 'True target orientation',
            line = dict({
                'color': 'rgb(180, 180, 180)',
                'dash': 'dashdot'
            })
        )
    )

    # target orientation
    frame['data'].append(
        go.Scatter(
            x = np.array([0., np.sin(target_orientation[k]) * follow_distance]) + target_position[1, k],
            y = np.array([0., np.cos(target_orientation[k]) * follow_distance]) + target_position[0, k],
            name = 'Target orientation',
            line = dict({
                'color': 'rgb(100, 100, 100)',
                'dash': 'dashdot'
            })
        )
    )

    # RAW FOLLOW POSITION
    # - - - - - - - - - -

    # raw follow position tail
    if plot_tails:
        frame['data'].append(
            go.Scatter(
                x = raw_follow_position[1, k_start:k_end],
                y = raw_follow_position[0, k_start:k_end],
                line = dict({
                    'color': 'rgba(99, 110, 250, 0.5)'  # px.colors.qualitative.Plotly[1]
                }),
                showlegend = False
            )
        )
    
    # raw follow position offset vector
    frame['data'].append(
        go.Scatter(
            x = [target_position[1, k], raw_follow_position[1, k]],
            y = [target_position[0, k], raw_follow_position[0, k]],
            line = dict({
                'color': px.colors.qualitative.Plotly[0],  # blue
                'dash': 'dash'
            }),
            showlegend = False
        )
    )

    # marker for raw follow position
    frame['data'].append(
        go.Scatter(
            x = [raw_follow_position[1, k]],
            y = [raw_follow_position[0, k]],
            marker = dict({
                'symbol': 'circle-open',
                'size': 20,
                'color': px.colors.qualitative.Plotly[0]  # blue
            }),
            name = 'Raw follow position'
        )
    )

    # FOLLOW POSITION
    # - - - - - - - -

    # position setpoint tail
    if plot_tails:
        frame['data'].append(
            go.Scatter(
                x = position_setpoint[1, k_start:k_end],
                y = position_setpoint[0, k_start:k_end],
                line = dict({
                    'color': 'rgba(239, 85, 59, 0.5)'  # px.colors.qualitative.Plotly[1]
                }),
                showlegend = False
            )
        )

    # position setpoint offset vector
    frame['data'].append(
        go.Scatter(
            x = [target_position[1, k], position_setpoint[1, k]],
            y = [target_position[0, k], position_setpoint[0, k]],
            line = dict({
                'color': px.colors.qualitative.Plotly[1],  # red
                'dash': 'dash'
            }),
            showlegend = False
        )
    )

    # marker for position setpoint
    frame['data'].append(
        go.Scatter(
            x = [position_setpoint[1, k]],
            y = [position_setpoint[0, k]],
            marker = dict({
                'symbol': 'circle',
                'size': 15,
                'color': px.colors.qualitative.Plotly[1]  # red
            }),
            name = 'Position setpoint'
        )
    )
    
    ################

    # append the frame
    fig_dict['frames'].append(frame)

    # update global axis range
    xaxis_max = np.max([xaxis_max, np.max(orbit_perimeter_x)])
    xaxis_min = np.min([xaxis_min, np.min(orbit_perimeter_x)])
    yaxis_max = np.max([yaxis_max, np.max(orbit_perimeter_y)])
    yaxis_min = np.min([yaxis_min, np.min(orbit_perimeter_y)])

    # set up the slider step corresponding to this frame
    slider_step = {
        'args': [
            [frame['name']],
            {
                'frame': {'duration': slider_step_duration, 'redraw': False},
                'mode': 'afterall',
                'transition': {'duration': slider_step_duration}
            }
        ],
        'label': frame['name'],
        'method': 'animate'
    }

    # append the slider step
    sliders_dict['steps'].append(slider_step)

# set the sliders
fig_dict['layout']['sliders'] = [sliders_dict]
 
# use the first frame for initial data view
fig_dict['data'] = fig_dict['frames'][0]['data']

## Show the 2D animation

In [685]:
fig = go.Figure(fig_dict)

# dimensions + title
fig.update_layout(
    width = 1200,
    height = 1000,
    title_text = f'Follow-me Positioning'
)

# Fix x axis & y axis scale to same value
# https://plotly.com/python/axes/#fixed-ratio-axes
# fig.update_yaxes (
#     scaleanchor = "x",
#     scaleratio = 1,
# )

# fix the xy range
fig['layout']['xaxis']['range'] = [xaxis_min, xaxis_max]
fig['layout']['yaxis']['range'] = [yaxis_min, yaxis_max]

fig.show()

## Debug] Angle Plotting

In [686]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=time_vector[:], y=follow_angles, name="Follow angle command"))
fig.add_trace(go.Scatter(x=time_vector[:], y=orbit_angle, name="Orbit angle"))
fig.add_trace(go.Scatter(x=time_vector[:], y=orbit_angle_raw, name="Orbit angle Raw"))
fig.add_trace(go.Scatter(x=time_vector[:], y=target_orientation, name="Tracked Target Orientation"))

fig.update_layout(title_text="Angle vs Time")

fig.show()

## Velocity timeseries

### Velocity Setpoint plotting (For checking sanity)

### Target Velocities

In [687]:
fig = go.Figure()

# Northing speed
fig.add_trace(
    go.Scatter(
        x = time_vector,
        y = target_velocity[0, :],
        name = 'Northing speed [m/s]'
    )
)

# Easting speed
fig.add_trace(
    go.Scatter(
        x = time_vector,
        y = target_velocity[1, :],
        name = 'Easting speed [m/s]'
    )
)

# update axis labels
fig['layout']['xaxis']['title'] = 'Time [s]'
fig['layout']['yaxis']['title'] = 'Speed [m/s]'

fig.show()

### Target speed


In [688]:
fig = go.Figure()

# threshold speed
fig.add_trace(
    go.Scatter(
        x = [time_vector[0], time_vector[-1]],
        y = [follow_me.get_speed_threshold(), follow_me.get_speed_threshold()],
        name = 'Speed threshold',
        line = dict({
            'color': 'rgb(0.7, 0.7, 0.7)',  # gray
            'dash': 'dash'            
        })
    )
)

# target speed
fig.add_trace(
    go.Scatter(
        x = time_vector,
        y = np.linalg.norm(target_velocity, axis=0),
        name = 'Target Speed',
        line = dict({
            'color': px.colors.qualitative.Plotly[0]  # blue
        }),
    )
)

# update axis labels
fig['layout']['xaxis']['title'] = 'Time [s]'
fig['layout']['yaxis']['title'] = 'Speed [m/s]'

fig.show()

## Angles

Target course vs. follow-me target orientation

In [689]:
fig = go.Figure()

# # True target orientation
# fig.add_trace(
#     go.Scatter(
#         x = time_vector,
#         y = np.rad2deg(target_orientation_truth),
#         name = 'Truth'
#     )
# )

# # Filtered target orientation
# fig.add_trace(
#     go.Scatter(
#         x = time_vector,
#         y = np.rad2deg(target_orientation),
#         name = 'Filtered'
#     )
# )

# Zero
fig.add_trace(
    go.Scatter(
        x = [time_vector[0], time_vector[-1]],
        y = [0, 0],
        line = dict({
            'color': 'rgb(0.7, 0.7, 0.7)',  # gray
            'dash': 'dash'
        }),
        showlegend = False
    )
)

# Target orientation error
fig.add_trace(
    go.Scatter(
        x = time_vector,
        y = np.rad2deg(wrap_pi(target_orientation_truth - target_orientation)),
        name = 'Error'
    )
)

# update axis labels
fig['layout']['xaxis']['title'] = 'Time [s]'
fig['layout']['yaxis']['title'] = 'Course angle [deg]'

fig.show()

Follow angle

In [690]:
fig = go.Figure()

# Zero
fig.add_trace(
    go.Scatter(
        x = [time_vector[0], time_vector[-1]],
        y = [0, 0],
        line = dict({
            'color': 'rgb(0.7, 0.7, 0.7)',  # gray
            'dash': 'dash'
        }),
        showlegend = False
    )
)

# Follow angle
fig.add_trace(
    go.Scatter(
        x = time_vector,
        # y = np.rad2deg(wrap_pi(follow_angles - follow_angle)),
        y = np.rad2deg(follow_angle),
        name = 'Follow Angle'
    )
)

# update axis labels
fig['layout']['xaxis']['title'] = 'Time [s]'
fig['layout']['yaxis']['title'] = 'Follow angle [deg]'

fig.show()

Orbit angle error

In [691]:
fig = go.Figure()

# Zero
fig.add_trace(
    go.Scatter(
        x = [time_vector[0], time_vector[-1]],
        y = [0, 0],
        line = dict({
            'color': 'rgb(0.7, 0.7, 0.7)',  # gray
            'dash': 'dash'
        }),
        showlegend = False
    )
)

# Orbit angle error
fig.add_trace(
    go.Scatter(
        x = time_vector,
        y = np.rad2deg(wrap_pi(orbit_angle_truth - orbit_angle)),
        name = 'Error'
    )
)

# update axis labels
fig['layout']['xaxis']['title'] = 'Time [s]'
fig['layout']['yaxis']['title'] = 'Orbit angle [deg]'

fig.show()